In [1]:
from utils.paths import *
# from utils.dataset import *
from utils.raster_utils import *

import plotly.express as px

In [12]:
n = 600  # rows
m = 1200  # cols

x = np.arange(m)
y = np.arange(n)

array = np.zeros([n,m])

array[ int( n/6) : int( 2*n/6), int( m/3) : int( 2*m/3) ] = 10
observer_height = 0
gps_coords = 46.04800, 7.64241
grid_size = 10
radius = 3000
path = '/Users/george-birchenough/sunmap_rasters/Switzerland_DEM_10m.tif'

array, observer_pixel, observer_height = get_square_masked_data(gps_coords, radius, grid_size, path)
array_cartesian = np.flip(array, axis=0)

fig = go.Figure()

fig.add_trace( dict(
            type = 'scatter',
            x = x,
            y = y
            )
)

fig.add_trace(dict(
            type = 'contour',
            x = x,
            y = y,
            z = array
        )
)


In [ ]:
# x_s = df.x * 1000 / n_steps
# y_s = (df.y * 1000 / n_steps)[::-1]
# z_s = df.shadow

z = array
x = np.arange(0, 2*radius+grid_size, grid_size)
y = x[::-1]

slope_array = np.gradient(z)
slope = ( ( np.array( slope_array[0]) **2 + np.array( slope_array[1]) **2 ) ** 0.5 ) / grid_size
slope = np.arctan(slope) * 180 / np.pi

fig = go.Figure()

fig.add_trace( dict(
        type = 'contour',
        z=z,
        x=x,
        y=y,
        contours = dict(
            start = z.min().round(100),
            end = z.max().round(100),
            size = 50,
            coloring = 'none',
            showlabels = True,
        ),
        showlegend = False,
    ))

fig.add_trace( dict(
        type = 'contour',
        z=z,
        x=x,
        y=y,
        contours = dict(
            start = z.min().round(10),
            end = z.max().round(10),
            size = 10,
            coloring = 'none',
            ),
        showlegend = False,
    ))
    
fig.update_layout(
    autosize = False,
    height = 800,
    width = 800,
    yaxis = dict(
            scaleanchor = 'x',
            scaleratio = 1
    ),
    xaxis = dict(
        range = [0, 2*radius]
    )
)

# fig.add_trace( dict(
#         type = 'heatmap',
#         z = z_s,
#         x= x_s,
#         y= y_s,
#         opacity = 0.5
#         # contours = dict(
#         #     start = array.min().round(10),
#         #     end = array.max().round(10),
#         #     size = 10,
#         #     coloring = 'none',
#         #     )
#     ))

def make_colormap(slope):
    range = slope.max() - slope.min()

    discrete_angles = np.array( [slope.min(), 30, 35, 40, 45, 50, 55, slope.max()] )

    norm_intervals = ( discrete_angles - slope.min() ) / range

    map = [(slope.min(),'white'), (30,'white'), (35,'#F0E54D'), (40,'#E4773B'), (45, '#CC2D5C'), (50, '#BF8CB8'), (55, '#524691'), (60, '#8BC4BF'),  (90, '#1D1D1B')]

    mapless = []
    for i in np.arange(len(map)):
        if map[i][0] < slope.max():
            mapless.append([ map[i][0], map[i][1] ] )
            largest_index = i

    mapless.append( [slope.max(), map[largest_index][1]] )


    dcolors = []
    for i in np.arange(len(mapless)):
        try:
            dcolors.append( [ (mapless[i][0]-slope.min())/range  , mapless[i][1] ] )
            dcolors.append( [ (mapless[i][0]-slope.min())/range  , mapless[i+1][1] ] )
        # print( i[0],i[1] )
        except:
            pass
    return dcolors

# dcolors = make_colormap(slope)
# fig.add_trace( dict(
#         type = 'heatmap',
#         z = slope,
#         x=x,
#         y=y,
#         colorscale = dcolors,
#         opacity = 0.5
#         # contours = dict(
#         #     start = array.min().round(10),
#         #     end = array.max().round(10),
#         #     size = 10,
#         #     coloring = 'none',
#         #     )
#     ))

fig.show()